In [3]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from dotenv import load_dotenv
from sqlalchemy import create_engine
import os

In [5]:
load_dotenv()
DB_PW = os.getenv('DB_PW')

# Database connection parameters
username = 'root'
password = DB_PW
host = 'localhost'
port = '3306'
database = 'hospital_register'

# Create SQLAlchemy engine
engine = create_engine(f'mysql+pymysql://{username}:{password}@{host}:{port}/{database}')

query = """
    SELECT name, beds_number, latitude, longitude
    FROM hospital_locations
    """

# Read data from SQL database into a DataFrame
df_hospitals = pd.read_sql(query, engine)

In [ ]:
df_places = pd.read_csv('../data/in/staging/atlas_places.csv')
df_places = df_places[['city', 'latitude', 'longitude']]

In [ ]:
def haversine(lat1, lon1, lat2, lon2):
    """
    Calculate the distance between two sets of latitude and longitude coordinates using the Haversine formula.
    """
    # Convert latitude and longitude to radians
    lat1_rad = np.radians(lat1)
    lon1_rad = np.radians(lon1)
    lat2_rad = np.radians(lat2)
    lon2_rad = np.radians(lon2)

    # Calculate the differences between the coordinates
    dlat = lat2_rad - lat1_rad
    dlon = lon2_rad - lon1_rad

    # Apply the Haversine formula
    a = np.sin(dlat / 2) ** 2 + np.cos(lat1_rad) * np.cos(lat2_rad) * np.sin(dlon / 2) ** 2
    c = 2 * np.arcsin(np.sqrt(a))
    r = 6371  # Radius of the Earth in kilometers

    # Calculate the distance
    distance = c * r

    return distance

# Calculate the distance to the nearest place in df_hospitals for each row in df_places
df_places['nearest_distance'] = df_places.apply(lambda row: np.min(haversine(row['latitude'], row['longitude'], df_hospitals['latitude'], df_hospitals['longitude'])), axis=1)

In [6]:
#df_places.to_csv('../data/in/staging/atlas_places_with_distance.csv', index=False)
df_places = pd.read_csv('../data/in/staging/atlas_places_with_distance.csv')
df_places['nearest_distance'] = df_places['nearest_distance'].round(1)

In [16]:
# Normalize the marker sizes
min_size = 5
max_size = 20
normalized_sizes = (df_hospitals['beds_number'] - df_hospitals['beds_number'].min()) / (df_hospitals['beds_number'].max() - df_hospitals['beds_number'].min()) * (max_size - min_size) + min_size

# Create the first layer
first_layer = go.Scattermapbox(
    lat=df_places['latitude'],
    lon=df_places['longitude'],
    mode='markers',
    marker=go.scattermapbox.Marker(
        size=10,  # Fixed size for the first layer markers
        color=df_places['nearest_distance'],  # Column for color scale
        colorscale='OrRd',  # Specify the color scale
        colorbar=dict(
            title=dict(text="Place [distance to nearest hospital]", side="top"),
            orientation='h',  # Horizontal orientation
            x=0.5,  # Center horizontally
            y=-0.125  # Position below the plot
        )
    ),
    text=df_places['city'],  # Hover text
    hoverinfo='text',
        hovertemplate=(
        "<b>City:</b> %{text}<br>" +
        "<b>Distance to nearest hospital:</b> %{marker.color} km"
    ),
    showlegend=False,
    name='',
)

# Create the second layer with a color scale and scaled marker sizes
second_layer = go.Scattermapbox(
    lat=df_hospitals['latitude'],
    lon=df_hospitals['longitude'],
    mode='markers',
    marker=go.scattermapbox.Marker(
        size=normalized_sizes,  # Scaled size of the markers
        color=df_hospitals['beds_number'],  # Column for color scale
        colorscale='Blugrn',  # Specify the color scale
        colorbar=dict(
            title=dict(text="Hospital [number of beds]", side="top"),
            orientation='h',  # Horizontal orientation
            x=0.5,  # Center horizontally
            y=-0.25  # Position below the first colorbar
        )
    ),
    text=df_hospitals['name'],  # Hover text
    hoverinfo='text',
        hovertemplate=(
        "<b>Hospital:</b> %{text}<br>" +
        "<b>Number of beds:</b> %{marker.color}"
    ),
    showlegend=False,
    name=''
)

# Create the figure and add both layers
fig = go.Figure()

fig.add_trace(first_layer)
fig.add_trace(second_layer)

# Update the layout
fig.update_layout(
    mapbox=dict(
        style="white-bg",  # Map style
        center=dict(lat=51.2, lon=10.5),  # Center of the map
        zoom=4.8  # Initial zoom level
    ),
    width=600,  # Set width in pixels
    height=800  # Set height in pixels
)

fig.show()
#fig.write_html("../resources/plotly_charts/hospital_distance_map.html")